# GG4257 - Urban Analytics
---
## Assignment 1 : Lab 2 Challenges
---


### Challenge No 1:

This challenge included 4 parts to it, so I will tackle each part one at a time.

1. Using a Dictionary, create a dataframe (table), with at least 4 columns and more than 100 rows. How come you can create this among data from scratch without defining every single row of data? 


In [26]:
import pandas as pd

#defining the dictionary
plants_dict = {
    'Name': ['Daisy', 'Dandelion', 'Nettle', 'Buttercup'],
    'Genre': ['Grown', 'Drama', 'Comedy', 'Thriller'],
    'Year': [2015, 2010, 2018, 2011],
    'Rating': [8.5, 7.8, 9.2, 8.0]
}

movie_ratings = pd.DataFrame(plants_dict, index = range(100))

df = pd.DataFrame(columns = ['a', 'b', 'c', 'd'], index = range(100))

ValueError: Length of values (4) does not match length of index (100)

Here we import pandas as pd, and then use this to define a new pandas data frame, with four columns (labelled a, b, c, and d) and giving the database an index range of 100. You can do this because the dataframe isn't technically empty, it's full of NA's.

2. Using the appropriate method, create a new DataFrame containing only the first 30 rows and the first 3 columns of the original DataFrame. Name this new DataFrame subset_df.


In [ ]:
subset_df = df.iloc[:30, :3]

3. Using the appropriate method, filter the rows from the original dataframe where a numerical attribute(column) is greater than a particular numerical value, and find another categorical attribute that is equal to a specific string or text. Name this new DataFrame filtered_df.


4. Check this website https://pandas.pydata.org/pandas-docs/stable/reference/api/pandas.DataFrame.mean.html and apply the methods, mean, standard deviation, group_by to run fundamental statistical analysis of your created data frame.

### Challenge No 2:

**Part No 1:**

1. Using the same workflow previously described, now calculate the clustered areas for the GeoPandasDataFrame `gdf_bikes_end`
2. Make sure you don't have any NaN in your columns, add a CRS, clean up the unnecessary attributes, calculate the cluster values, and plot a map of 4 calculated clusters for the return locations.

In [40]:
# importing everything we need!!
import requests
import pandas as pd
import geopandas as gpd
from sklearn.cluster import KMeans
import leafmap
from shapely.geometry import Point

In [33]:
# code from the labbook to set us up to use the gdf_bikes_end dataframe!

url_bikes = "https://api.glasgow.gov.uk/mobility/v1/get_rentals?startDate=2022-05-01&endDate=2023-05-01"
response = requests.get(url_bikes)
data = response.json() #response is 200 so it worked!
rental_data = data['data']
rental_pd = pd.DataFrame(rental_data)
clean_rental_pd = rental_pd.dropna(subset=['startPlaceLat', 'startPlaceLong', 'endPlaceLat','endPlaceLong'])
gdf_bikes_end = gpd.GeoDataFrame(clean_rental_pd, geometry=gpd.points_from_xy(clean_rental_pd['endPlaceLong'], clean_rental_pd['endPlaceLat']))

In [34]:
gdf_bikes_end.info() #having a look at all of the columns we have

<class 'geopandas.geodataframe.GeoDataFrame'>
Index: 9940 entries, 0 to 9999
Data columns (total 25 columns):
 #   Column                   Non-Null Count  Dtype   
---  ------                   --------------  -----   
 0   created                  9940 non-null   object  
 1   updated                  9940 non-null   object  
 2   cityId                   9940 non-null   object  
 3   bikeId                   9940 non-null   object  
 4   startDate                9940 non-null   object  
 5   startPlaceId             9940 non-null   object  
 6   startPlaceCityId         9940 non-null   object  
 7   startPlaceName           9940 non-null   object  
 8   startPlaceStationNumber  9555 non-null   float64 
 9   startPlaceLat            9940 non-null   float64 
 10  startPlaceLong           9940 non-null   float64 
 11  startChannelId           0 non-null      object  
 12  endDate                  9940 non-null   object  
 13  endPlaceId               9940 non-null   object  
 14  endPl

In [35]:
keep_cols = [
    "bikeId",
    "endDate",
    "endPlaceName",
    "endPlaceLat",
    "endPlaceLong",
    "geometry"
]
#the above lines of code clean up the data and just keep a few columns that could be relevant to this analysis

clean_gdf_bikes_end = gdf_bikes_end[keep_cols]
clean_gdf_bikes_end.head()

bikeId               endDate  \
0  116870  2022-05-01T00:02:36Z   
1  143384  2022-05-01T00:22:34Z   
2  129744  2022-05-01T00:10:08Z   
3  143168  2022-05-01T02:57:49Z   
4  143248  2022-05-01T01:21:31Z   

                                        endPlaceName  endPlaceLat  \
0                              ELECTRIC - Broomielaw    55.856600   
1  Alexandra Park (south entrance) Alexandra Para...    55.863128   
2                         Botanic Gardens - ELECTRIC    55.878278   
3                 ELECTRIC - Cessnock Subway Station    55.851918   
4                         ELECTRIC - St Enoch Square    55.856829   

   endPlaceLong                   geometry  
0     -4.263521  POINT (-4.26352 55.85660)  
1     -4.210282  POINT (-4.21028 55.86313)  
2     -4.288487  POINT (-4.28849 55.87828)  
3     -4.294490  POINT (-4.29449 55.85192)  
4     -4.255292  POINT (-4.25529 55.85683)

In [41]:
# projecting the data!! creating latitude and longitude pairs and then projecting them into the right CRS
geom = [Point(xy) for xy in zip(clean_gdf_bikes_end.endPlaceLong, clean_gdf_bikes_end.endPlaceLat)]
projected_gdf_bikes_end = gpd.GeoDataFrame(clean_gdf_bikes_end, crs='EPSG:4326', geometry=geom)
projected_gdf_bikes_end.explore()

In [42]:
noClusters = 4 #we want 4 cluster areas
kmeans_collection = KMeans(n_clusters=noClusters, random_state=42)
projected_gdf_bikes_end['kmeans_cluster'] = kmeans_collection.fit_predict(projected_gdf_bikes_end[['endPlaceLong', 'endPlaceLat']])

In [43]:
projected_gdf_bikes_end.head()

bikeId               endDate  \
0  116870  2022-05-01T00:02:36Z   
1  143384  2022-05-01T00:22:34Z   
2  129744  2022-05-01T00:10:08Z   
3  143168  2022-05-01T02:57:49Z   
4  143248  2022-05-01T01:21:31Z   

                                        endPlaceName  endPlaceLat  \
0                              ELECTRIC - Broomielaw    55.856600   
1  Alexandra Park (south entrance) Alexandra Para...    55.863128   
2                         Botanic Gardens - ELECTRIC    55.878278   
3                 ELECTRIC - Cessnock Subway Station    55.851918   
4                         ELECTRIC - St Enoch Square    55.856829   

   endPlaceLong                   geometry  kmeans_cluster  
0     -4.263521  POINT (-4.26352 55.85660)               3  
1     -4.210282  POINT (-4.21028 55.86313)               0  
2     -4.288487  POINT (-4.28849 55.87828)               1  
3     -4.294490  POINT (-4.29449 55.85192)               1  
4     -4.255292  POINT (-4.25529 55.85683)               3

In [46]:
bikeMap = leafmap.Map(center=(55.860166, -4.257505),
                zoom=12,
                draw_control=False,
                measure_control=False,
                fullscreen_control=False,
                attribution_control=True,)

bikeMap.add_basemap("CartoDB.Positron")
bikeMap.add_data(projected_gdf_bikes_end, column='kmeans_cluster',legend_title='Clusters',cmap='Set1',k=4,)

#Ploting the map
bikeMap

Map(center=[55.860166, -4.257505], controls=(AttributionControl(options=['position', 'prefix'], position='bott…

**Part No 2:**

1. Using the Glasglow Open Data API ( Transit) https://developer.glasgow.gov.uk/api-details#api=traffic&operation=traffic-sensor-locations fetch all the sensor locations in the city.
2. Map the sensor
3. Find the WorkingZones and Calculate/Map the areas with more and fewer sensors distributed in the city.
4. You will need:
   * Get two separate Geopandas DataFrames, one for the traffic sensors and another one for the WorkingZones.
   * Using `sJoin` ( Spatial Join) https://geopandas.org/en/stable/docs/reference/api/geopandas.sjoin.html
   calculate the overlay of sensors and polygons.
   * Using group_by https://pandas.pydata.org/pandas-docs/stable/reference/api/pandas.DataFrame.groupby.html to count the number of sensors per WorkingZone
   * Make sure you add the counts into the WorkingZone polygons of Glasgow so you can create a map of Zones with more and fewer traffic sensors.
   * Of course, you will need extra steps where you manipulate the data and extract what you need, for instance, clipping the Working Zones only for Glasgow.
5. Make sure you comment on your code and describe how you are manipulating the data.


In [18]:
# using API to retrieve data
url_sensors = "https://api.glasgow.gov.uk/traffic/v1/movement/sites"
response = requests.get(url_sensors) #result is 200 so we know the request works!
data = response.json()
dataupdate = data["siteId"]

TypeError: list indices must be integers or slices, not str